# Dependencies

In [1]:
!git clone https://github.com/davepvelasco/fastquant.git

# Install necessary packages
!pip install pandas-ta optuna yfinance ./fastquant

fatal: destination path 'fastquant' already exists and is not an empty directory.
Processing ./fastquant
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.1/115.1 kB 1.6 MB/s eta 0:00:00a 0:00:01
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 948.2/948.2 kB 45.9 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 79.2/79.2 kB 8.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 117.7/117.7 kB 12.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 364.4/364.4 kB 28.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 104.7/104.7 kB 11.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 233.5/233.5 kB 22.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 419.5/419.5 kB 31.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━

# Model Development

In [2]:
import random
from pathlib import Path

import numpy as np
import optuna
import pandas as pd
import tensorflow as tf
from sklearn.preprocessing import MinMaxScaler
from tensorflow.keras.layers import LSTM, Dense
from tensorflow.keras.models import Sequential

# GPU optimization settings
gpus = tf.config.list_physical_devices("GPU")
if gpus:
    try:
        for gpu in gpus:
            tf.config.experimental.set_memory_growth(gpu, True)
        logical_gpus = tf.config.list_logical_devices("GPU")
        print(len(gpus), "Physical GPUs,", len(logical_gpus), "Logical GPUs")
    except RuntimeError as e:
        print(e)

STOCKS = [
    "AC",
    "ACEN",
    "AEV",
    "AGI",
    "ALI",
    "BDO",
    "BLOOM",
    "BPI",
    "CNPF",
    "CNVRG",
    "DMC",
    "EMI",
    "GLO",
    "GTCAP",
    "ICT",
    "JFC",
    "JGS",
    "LTG",
    "MBT",
    "MER",
    "MONDE",
    "NIKL",
    "PGOLD",
    "SCC",
    "SM",
    "SMC",
    "SMPH",
    "TEL",
    "URC",
    "WLCON",
]

# Set random seed for reproducibility
RANDOM_SEED = 42
random.seed(RANDOM_SEED)
np.random.seed(RANDOM_SEED)
tf.random.set_seed(RANDOM_SEED)

# Parameters
sequence_length = 60
features = ["Open", "Close", "spread"]
target = "target"
epochs = 50
trials = 50

# Helper function to load stock data
def load_stock_data(ticker, data_dir="data"):
    file_path = Path(data_dir) / f"{ticker}.csv"
    if not file_path.exists():
        raise FileNotFoundError(f"CSV file for {ticker} not found at {file_path}.")

    # Load the CSV file
    df = pd.read_csv(file_path, parse_dates=["Date"], index_col="Date")

    # Remove commas and convert columns to numeric
    for col in df.columns:
        df[col] = df[col].replace(",", "", regex=True).astype(float)

    return df

# Helper function to prepare data for a single stock
def prepare_stock_data(stock, sequence_length, features, target):
    # Load data
    df = load_stock_data(stock)

    # Check if the start year is 2004 and the end year is 2024
    start_date = df.index.min()
    end_date = df.index.max()
    if not (start_date.year == 2004 and end_date.year == 2024):
        print(
            f"Excluding {stock} due to date range: {start_date.date()} to {end_date.date()}"
        )
        return None  # Early return if criteria not met

    # Add spread feature and remove "High" and "Low" columns
    df["spread"] = df["High"] - df["Low"]
    df.drop(columns=["High", "Low"], inplace=True)

    df["target"] = df["Close"].shift(-1)  # Shift target to predict next close
    df.dropna(inplace=True)

    # Split data
    train_size = int(0.6 * len(df))
    val_size = int(0.2 * len(df))
    train_df = df[:train_size]
    val_df = df[train_size : train_size + val_size]
    test_df = df[train_size + val_size :]

    # Print date ranges
    print(f"Stock: {stock}")
    print(f"  Train set: {train_df.index[0]} to {train_df.index[-1]}")
    print(f"  Validation set: {val_df.index[0]} to {val_df.index[-1]}")
    print(f"  Test set: {test_df.index[0]} to {test_df.index[-1]}")

    # Scale the data
    scaler = MinMaxScaler()
    train_scaled = pd.DataFrame(
        scaler.fit_transform(train_df), columns=train_df.columns, index=train_df.index
    )
    val_scaled = pd.DataFrame(
        scaler.transform(val_df), columns=val_df.columns, index=val_df.index
    )
    test_scaled = pd.DataFrame(
        scaler.transform(test_df), columns=test_df.columns, index=test_df.index
    )

    # Create rolling windows
    def create_rolling_windows(data, seq_len, feature_cols, target_col):
        X, y = [], []
        for i in range(len(data) - seq_len):
            X.append(data.iloc[i : i + seq_len][feature_cols].values)
            y.append(data.iloc[i + seq_len][target_col])
        return np.array(X), np.array(y)

    X_train, y_train = create_rolling_windows(
        train_scaled, sequence_length, features, target
    )
    X_val, y_val = create_rolling_windows(val_scaled, sequence_length, features, target)
    X_test, y_test = create_rolling_windows(
        test_scaled, sequence_length, features, target
    )

    return X_train, y_train, X_val, y_val, X_test, y_test, scaler, df, test_df


# Prepare data for all stocks
stock_data = {}
for stock in STOCKS:
    result = prepare_stock_data(stock, sequence_length, features, target)
    if result is not None:  # Only include stocks that pass the criteria
        stock_data[stock] = result

# Define the objective function for Optuna
def objective(trial):
    # Updated hyperparameter search space
    num_layers = trial.suggest_int("num_layers", 1, 3)  # Variable number of layers
    lstm_units = trial.suggest_int("lstm_units", 10, 100)
    dense_units = trial.suggest_int("dense_units", 1, 50)
    learning_rate = trial.suggest_float("learning_rate", 1e-4, 1e-2, log=True)  # Adjusted range
    batch_size = trial.suggest_categorical("batch_size", [16, 32, 64, 128])
    dropout_rate = trial.suggest_float("dropout_rate", 0.0, 0.5)

    # Build the LSTM model dynamically based on the number of layers
    model = Sequential()
    for i in range(num_layers):
        # Add LSTM layers
        if i == 0:  # First layer requires input shape
            model.add(
                LSTM(
                    lstm_units,
                    activation="tanh",
                    recurrent_activation="sigmoid",
                    input_shape=(sequence_length, len(features)),
                    dropout=dropout_rate,
                    return_sequences=(i < num_layers - 1),  # Return sequences if more layers follow
                )
            )
        else:
            model.add(
                LSTM(
                    lstm_units,
                    activation="tanh",
                    recurrent_activation="sigmoid",
                    dropout=dropout_rate,
                    return_sequences=(i < num_layers - 1),
                )
            )
    model.add(Dense(dense_units, activation="relu"))
    model.add(Dense(1))  # Output layer

    # Compile the model
    optimizer = tf.keras.optimizers.Adam(learning_rate=learning_rate)
    model.compile(optimizer=optimizer, loss="mse")

    # Use a single stock for tuning
    tuning_stock = STOCKS[0]
    if tuning_stock not in stock_data:
        return float("inf")

    X_train, y_train, X_val, y_val, _, _, _, _, _ = stock_data[tuning_stock]

    # Train the model
    model.fit(
        X_train,
        y_train,
        batch_size=batch_size,
        epochs=50,
        validation_data=(X_val, y_val),
        verbose=0,
        shuffle=True,
    )

    # Evaluate the model on the validation set
    val_loss = model.evaluate(X_val, y_val, verbose=0)
    return val_loss

# Optimize with Optuna
study = optuna.create_study(direction="minimize")
study.optimize(objective, n_trials=trials)

# Print the best trial
best_trial = study.best_trial
print(f"Best trial: {best_trial.number}")
print("  Value (val_loss):", best_trial.value)
print("  Params:", best_trial.params)

# Train the best model on all stocks
best_params = best_trial.params
model = Sequential(
    [
        LSTM(
            best_params["lstm_units"],
            activation="tanh",
            recurrent_activation="sigmoid",
            input_shape=(sequence_length, len(features)),
            dropout=best_params["dropout_rate"],
        ),
        Dense(best_params["dense_units"], activation="relu"),
        Dense(1),
    ]
)
optimizer = tf.keras.optimizers.Adam(learning_rate=best_params["learning_rate"])
model.compile(optimizer=optimizer, loss="mse")

for epoch in range(epochs):
    print(f"Epoch {epoch + 1}/{epochs}")
    for stock, data in stock_data.items():
        X_train, y_train, X_val, y_val, _, _, _, _, _ = data
        model.fit(
            X_train,
            y_train,
            batch_size=best_params["batch_size"],
            validation_data=(X_val, y_val),
            verbose=1,
            shuffle=True,
        )

# Save the final model
checkpoint_path = "model.keras"
model.save(checkpoint_path)
print(f"Best model saved to {checkpoint_path}")


2025-01-17 04:40:44.808478: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2025-01-17 04:40:44.808574: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2025-01-17 04:40:44.811192: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-01-17 04:40:44.826110: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2025-01-17 04:40:46.528344: W tensorflow/compiler/tf2

1 Physical GPUs, 1 Logical GPUs
Stock: AC
  Train set: 2004-01-05 00:00:00 to 2016-07-29 00:00:00
  Validation set: 2016-08-01 00:00:00 to 2020-10-14 00:00:00
  Test set: 2020-10-15 00:00:00 to 2024-12-26 00:00:00
Stock: ACEN
  Train set: 2004-01-06 00:00:00 to 2016-11-25 00:00:00
  Validation set: 2016-11-28 00:00:00 to 2020-12-18 00:00:00
  Test set: 2020-12-21 00:00:00 to 2024-12-26 00:00:00
Stock: AEV
  Train set: 2004-01-06 00:00:00 to 2016-08-25 00:00:00
  Validation set: 2016-08-26 00:00:00 to 2020-10-28 00:00:00
  Test set: 2020-10-29 00:00:00 to 2024-12-26 00:00:00
Stock: AGI
  Train set: 2004-07-02 00:00:00 to 2017-08-23 00:00:00
  Validation set: 2017-08-24 00:00:00 to 2021-05-06 00:00:00
  Test set: 2021-05-07 00:00:00 to 2024-12-26 00:00:00
Stock: ALI
  Train set: 2004-01-05 00:00:00 to 2016-07-29 00:00:00
  Validation set: 2016-08-01 00:00:00 to 2020-10-14 00:00:00
  Test set: 2020-10-15 00:00:00 to 2024-12-26 00:00:00
Stock: BDO
  Train set: 2004-01-05 00:00:00 to 2016-0

[I 2025-01-17 04:41:35,275] A new study created in memory with name: no-name-bbe2ffd5-20d7-47bd-bf82-813bba40b492


Excluding WLCON due to date range: 2017-03-31 to 2024-12-27


2025-01-17 04:41:41.567508: I external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:454] Loaded cuDNN version 8907
2025-01-17 04:41:42.668841: I external/local_xla/xla/service/service.cc:168] XLA service 0x7f5b7c0039e0 initialized for platform CUDA (this does not guarantee that XLA will be used). Devices:
2025-01-17 04:41:42.668914: I external/local_xla/xla/service/service.cc:176]   StreamExecutor device (0): Quadro RTX 4000, Compute Capability 7.5
2025-01-17 04:41:42.679922: I tensorflow/compiler/mlir/tensorflow/utils/dump_mlir_util.cc:269] disabling MLIR crash reproducer, set env var `MLIR_CRASH_REPRODUCER_DIRECTORY` to enable.
I0000 00:00:1737088902.864941     146 device_compiler.h:186] Compiled cluster using XLA!  This line is logged at most once for the lifetime of the process.
[I 2025-01-17 04:42:41,628] Trial 0 finished with value: 0.038261134177446365 and parameters: {'num_layers': 1, 'lstm_units': 93, 'dense_units': 13, 'learning_rate': 0.0008027639397238166, 'batch_size': 3

Best trial: 18
  Value (val_loss): 0.0010901620844379067
  Params: {'num_layers': 1, 'lstm_units': 67, 'dense_units': 31, 'learning_rate': 0.0003633599861207184, 'batch_size': 16, 'dropout_rate': 0.0014425223390655542}
Epoch 1/50
182/182 [==============================] - 2s 13ms/step - loss: 1.8324e-04 - val_loss: 5.5105e-04
Epoch 2/50
182/182 [==============================] - 2s 13ms/step - loss: 1.9677e-04 - val_loss: 5.3627e-04
Epoch 3/50
182/182 [==============================] - 2s 13ms/step - loss: 2.0735e-04 - val_loss: 5.2973e-04
Epoch 4/50
182/182 [==============================] - 3s 14ms/step - loss: 1.3018e-04 - val_loss: 3.9343e-04
Epoch 5/50
182/182 [==============================] - 3s 14ms/step - loss: 1.3057e-04 - val_loss: 3.8811e-04
Epoch 6/50
182/182 [==============================] - 2s 13ms/step - loss: 1.3009e-04 - val_loss: 3.7623e-04
Epoch 7/50
182/182 [==============================] - 2s 13ms/step - loss: 1.3348e-04 - val_loss: 3.8422e-04
Epoch 8/50
182/182

# Model Evaluation

In [3]:
from sklearn.metrics import mean_squared_error
from tensorflow.keras.models import load_model
import matplotlib.pyplot as plt


# Function to evaluate the model on the test set
def evaluate_model(stock, data):
    print(f"Evaluating model for {stock}...")
    _, _, _, _, X_test, y_test, scaler, df, test_df = data

    # Predict on the test set
    predictions = model.predict(X_test)

    # Reverse scaling for y_test and predictions
    n_columns = df.shape[1]
    padded_y_test = np.zeros((len(y_test), n_columns))
    padded_predictions = np.zeros((len(predictions), n_columns))

    padded_y_test[:, -1] = y_test
    padded_predictions[:, -1] = predictions.flatten()

    y_test_original = scaler.inverse_transform(padded_y_test)[:, -1]
    predictions_original = scaler.inverse_transform(padded_predictions)[:, -1]

    # Calculate RMSE
    rmse = np.sqrt(mean_squared_error(y_test_original, predictions_original))
    print(f"{stock}: RMSE = {rmse:.2f}")

    # Reset Matplotlib settings
    plt.rcParams.update(plt.rcParamsDefault)

    # Plot predictions vs actual values
    plt.figure(figsize=(14, 6))
    plt.plot(test_df.iloc[sequence_length:].index, y_test_original, label="True Close Price")
    plt.plot(test_df.iloc[sequence_length:].index, predictions_original, label="Predicted Close Price", alpha=0.7)
    plt.title(f"{stock}: Actual vs Predicted Close Prices (RMSE: {rmse:.2f})")
    plt.xlabel("Date")
    plt.ylabel("Price")
    plt.legend()

    # Save the plot to the output directory
    plot_path = f"predictions/{stock}_evaluation_plot.png"
    plt.savefig(plot_path, dpi=300, bbox_inches="tight")
    print(f"Plot saved for {stock} to {plot_path}")
    plt.close()

for stock, data in stock_data.items():
    evaluate_model(stock, data)  # Evaluate the model on the test set

Evaluating model for AC...
31/31 [==============================] - 1s 5ms/step
AC: RMSE = 17.79
Plot saved for AC to predictions/AC_evaluation_plot.png
Evaluating model for ACEN...
29/29 [==============================] - 0s 5ms/step
ACEN: RMSE = 0.38
Plot saved for ACEN to predictions/ACEN_evaluation_plot.png
Evaluating model for AEV...
30/30 [==============================] - 0s 5ms/step
AEV: RMSE = 1.44
Plot saved for AEV to predictions/AEV_evaluation_plot.png
Evaluating model for AGI...
27/27 [==============================] - 0s 5ms/step
AGI: RMSE = 0.29
Plot saved for AGI to predictions/AGI_evaluation_plot.png
Evaluating model for ALI...
31/31 [==============================] - 0s 5ms/step
ALI: RMSE = 0.94
Plot saved for ALI to predictions/ALI_evaluation_plot.png
Evaluating model for BDO...
31/31 [==============================] - 0s 5ms/step
BDO: RMSE = 5.77
Plot saved for BDO to predictions/BDO_evaluation_plot.png
Evaluating model for BLOOM...
20/20 [==========================

# PSEi Performance (For benchmark)

In [4]:
import yfinance as yf
import pandas as pd
import numpy as np

# Annual risk-free rate (20-year Philippine bond yield)
# https://ph.investing.com/rates-bonds/philippines-20-year-bond-yield
annual_risk_free_rate_20yr = 0.06221

# Convert annual to daily risk-free rate (252 trading days/year)
daily_risk_free_rate = (1 + annual_risk_free_rate_20yr) ** (1 / 252) - 1

# Define PSEi ticker
psei_ticker = "PSEI.PS"

# Download PSEi data
psei_data = yf.download(psei_ticker, start="2004-01-01", end="2024-12-31")
if psei_data.empty:
    raise ValueError("Failed to download PSEi data.")

# Calculate daily returns
psei_data["Returns"] = psei_data["Close"].pct_change()

# Calculate excess returns
psei_data["Excess_Return"] = psei_data["Returns"] - daily_risk_free_rate

# Drop NaN values
psei_data = psei_data.dropna()

# Mean and std of daily excess returns
mean_excess_return = psei_data["Excess_Return"].mean()
std_excess_return = psei_data["Excess_Return"].std()

# Daily Sharpe ratio
sharpe_ratio = mean_excess_return / std_excess_return

# Annualize mean return (252 trading days)
annualized_mean_excess_return = mean_excess_return * 252

# Annualize std (volatility scales with sqrt(252))
annualized_std_excess_return = std_excess_return * (252 ** 0.5)

# Annualized Sharpe ratio
annualized_sharpe_ratio = annualized_mean_excess_return / annualized_std_excess_return

# Print results
print(f"Daily Risk-Free Rate: {daily_risk_free_rate:.6f}")
print(f"Mean Excess Return (Daily): {mean_excess_return:.6f}")
print(f"Std Dev of Excess Returns (Daily): {std_excess_return:.6f}")
print(f"Daily Sharpe Ratio: {sharpe_ratio:.6f}")
print(f"Annualized Mean Excess Return: {annualized_mean_excess_return:.6f}")
print(f"Annualized Std Dev of Excess Returns: {annualized_std_excess_return:.6f}")
print(f"Annualized Sharpe Ratio: {annualized_sharpe_ratio:.6f}")


[*********************100%***********************]  1 of 1 completed

Daily Risk-Free Rate: 0.000240
Mean Excess Return (Daily): 0.000132
Std Dev of Excess Returns (Daily): 0.012558
Daily Sharpe Ratio: 0.010526
Annualized Mean Excess Return: 0.033310
Annualized Std Dev of Excess Returns: 0.199348
Annualized Sharpe Ratio: 0.167093


# LSTM Strategy (With Comissions)

In [5]:
from fastquant import backtest

def run_backtesting(stock, data):
    print(f"Running backtesting for {stock}...")
    X_train, y_train, X_val, y_val, X_test, y_test, scaler, df, _ = data

    # Prepare the entire dataset for predictions
    all_X = np.concatenate([X_train, X_val, X_test], axis=0)
    all_predictions = model.predict(all_X)

    # Reverse scaling for predictions
    n_columns = df.shape[1]
    padded_all_predictions = np.zeros((len(all_predictions), n_columns))
    padded_all_predictions[:, -1] = all_predictions.flatten()

    all_predictions_original = scaler.inverse_transform(padded_all_predictions)[:, -1]

    # Align predictions with the dataset
    # We need to exclude the first sequence_length rows from df
    prediction_start_idx = sequence_length  # Skip initial rows used for the first sequence
    df_full = df.iloc[prediction_start_idx : prediction_start_idx + len(all_predictions)].copy()

    # Sanity check for alignment
    if len(df_full) != len(all_predictions_original):
        raise ValueError(
            f"Prediction length ({len(all_predictions_original)}) does not match dataset length ({len(df_full)})."
        )

    # Add predictions and calculate expected percentage changes
    df_full['predicted_close'] = all_predictions_original
    df_full['expected_pct_change'] = (df_full['predicted_close'] - df_full['Close']) / df_full['Close'] * 100
    df_full['custom'] = df_full['expected_pct_change'] * -1  # Negative for backtest format

    # Backtest using the full dataset
    columns_to_keep = [
        "rtot", "ravg", "rnorm", "rnorm100", "len", "drawdown", "moneydown", "maxdrawdown",
        "maxdrawdownperiod", "sharperatio", "pnl", "final_value", "total", "win_rate", "won",
        "lost", "won_avg", "won_avg_prcnt", "lost_avg", "lost_avg_prcnt", "won_max_prcnt",
        "lost_max_prcnt"
    ]
    sorted_combined_df, history_dict, fig = backtest("custom", df_full.dropna(), upper_limit=2, lower_limit=-2, return_history=True, return_plot=True, commission=0.006, verbose=False, riskfreerate=annual_risk_free_rate_20yr)

    # Save plot
    output_path = f"results/lstm/{stock}_plot.png"
    fig.savefig(output_path)
    
    # Keep relevant analytics
    analytics = sorted_combined_df[columns_to_keep]
    analytics['ticker'] = stock

    # Save order history
    columns_to_keep = ["type", "price", "size", "order_value", "portfolio_value", "commission", "pnl"]
    history_dict["orders"][columns_to_keep].to_csv(f"results/lstm/{stock}_orders.csv", index=False)

    return analytics


# Main loop: evaluate model first, then backtest
all_analytics = []

for stock, data in stock_data.items():
    analytics = run_backtesting(stock, data)  # Backtest on the entire dataset
    all_analytics.append(analytics)

# Combine all analytics into a single DataFrame
final_analytics_df = pd.concat(all_analytics, ignore_index=True)

# Save the combined DataFrame as a single CSV
final_output_path = "results/lstm/combined_analytics.csv"
final_analytics_df.to_csv(final_output_path, index=False)

print(f"Combined analytics CSV saved to {final_output_path}")

Running backtesting for AC...
155/155 [==============================] - 1s 5ms/step
===Strategy level arguments===
Upper limit:  2
Lower limit:  -2


<IPython.core.display.Javascript object>

Running backtesting for ACEN...
149/149 [==============================] - 1s 5ms/step
===Strategy level arguments===
Upper limit:  2
Lower limit:  -2


<IPython.core.display.Javascript object>

Running backtesting for AEV...
154/154 [==============================] - 1s 5ms/step
===Strategy level arguments===
Upper limit:  2
Lower limit:  -2


...

Running backtesting for TEL...
155/155 [==============================] - 1s 5ms/step
===Strategy level arguments===
Upper limit:  2
Lower limit:  -2


<IPython.core.display.Javascript object>

Running backtesting for URC...
149/149 [==============================] - 1s 5ms/step
===Strategy level arguments===
Upper limit:  2
Lower limit:  -2


<IPython.core.display.Javascript object>

Combined analytics CSV saved to results/lstm/combined_analytics.csv


In [6]:
import pandas as pd

# Portfolio-Level Statistics
total_pnl = final_analytics_df['pnl'].sum()
final_portfolio_value = final_analytics_df['final_value'].sum()
average_sharpe_ratio = final_analytics_df['sharperatio'].mean()
average_return = final_analytics_df['rtot'].mean()
average_annualized_return = final_analytics_df['rnorm100'].mean()
max_drawdown = final_analytics_df['maxdrawdown'].max()

# Risk Metrics
total_trades = final_analytics_df['total'].sum()
total_wins = final_analytics_df['won'].sum()
win_rate = total_wins / total_trades if total_trades > 0 else 0
average_loss = final_analytics_df['lost_avg_prcnt'].mean()
max_loss = final_analytics_df['lost_max_prcnt'].min()

# Performance Metrics
most_profitable_stock = final_analytics_df.loc[final_analytics_df['pnl'].idxmax(), 'ticker']
highest_win = final_analytics_df['won_max_prcnt'].max()
most_loss_stock = final_analytics_df.loc[final_analytics_df['lost_avg_prcnt'].idxmin(), 'ticker']


# Print Portfolio Insights
print("Portfolio Insights:")
print(f"Total Profit (PnL): {total_pnl}")
print(f"Final Portfolio Value: {final_portfolio_value}")
print(f"Average Sharpe Ratio: {average_sharpe_ratio}")
print(f"Average Return: {average_return}")
print(f"Average Annualized Return (rnorm100): {average_annualized_return}")
print(f"Max Drawdown: {max_drawdown}")
print(f"Win Rate: {win_rate * 100:.2f}%")
print(f"Average Loss (%): {average_loss}")
print(f"Max Loss (%): {max_loss}")
print(f"Most Profitable Stock: {most_profitable_stock}")
print(f"Highest Win (% Gain): {highest_win}")
print(f"Most Loss (% Stock): {most_loss_stock}")


Portfolio Insights:
Total Profit (PnL): 22782311.729999997
Final Portfolio Value: 24782311.741450008
Average Sharpe Ratio: 0.18994939199663374
Average Return: 1.636590559464532
Average Annualized Return (rnorm100): 9.284804779235737
Max Drawdown: 98.10795658699925
Win Rate: 64.96%
Average Loss (%): -14.865622680816696
Max Loss (%): -1178.4602454800004
Most Profitable Stock: DMC
Highest Win (% Gain): 2712.87176194
Most Loss (% Stock): DMC


# LSTM Strategy (Without Commisions)

In [7]:
from fastquant import backtest

def run_backtesting(stock, data):
    print(f"Running backtesting for {stock}...")
    X_train, y_train, X_val, y_val, X_test, y_test, scaler, df, _ = data

    # Prepare the entire dataset for predictions
    all_X = np.concatenate([X_train, X_val, X_test], axis=0)
    all_predictions = model.predict(all_X)

    # Reverse scaling for predictions
    n_columns = df.shape[1]
    padded_all_predictions = np.zeros((len(all_predictions), n_columns))
    padded_all_predictions[:, -1] = all_predictions.flatten()

    all_predictions_original = scaler.inverse_transform(padded_all_predictions)[:, -1]

    # Align predictions with the dataset
    # We need to exclude the first `sequence_length` rows from `df`
    prediction_start_idx = sequence_length  # Skip initial rows used for the first sequence
    df_full = df.iloc[prediction_start_idx : prediction_start_idx + len(all_predictions)].copy()

    # Sanity check for alignment
    if len(df_full) != len(all_predictions_original):
        raise ValueError(
            f"Prediction length ({len(all_predictions_original)}) does not match dataset length ({len(df_full)})."
        )

    # Add predictions and calculate expected percentage changes
    df_full['predicted_close'] = all_predictions_original
    df_full['expected_pct_change'] = (df_full['predicted_close'] - df_full['Close']) / df_full['Close'] * 100
    df_full['custom'] = df_full['expected_pct_change'] * -1  # Negative for backtest format

    # Backtest using the full dataset
    columns_to_keep = [
        "rtot", "ravg", "rnorm", "rnorm100", "len", "drawdown", "moneydown", "maxdrawdown",
        "maxdrawdownperiod", "sharperatio", "pnl", "final_value", "total", "win_rate", "won",
        "lost", "won_avg", "won_avg_prcnt", "lost_avg", "lost_avg_prcnt", "won_max_prcnt",
        "lost_max_prcnt"
    ]
    sorted_combined_df, history_dict, fig = backtest("custom", df_full.dropna(), upper_limit=2, lower_limit=-2, return_history=True, return_plot=True, verbose=False, riskfreerate=annual_risk_free_rate_20yr)

    # Save plot
    output_path = f"results/lstm_no_commission/{stock}_plot.png"
    fig.savefig(output_path)
    
    # Keep relevant analytics
    analytics = sorted_combined_df[columns_to_keep]
    analytics['ticker'] = stock

    # Save order history
    columns_to_keep = ["type", "price", "size", "order_value", "portfolio_value", "commission", "pnl"]
    history_dict["orders"][columns_to_keep].to_csv(f"results/lstm_no_commission/{stock}_orders.csv", index=False)

    return analytics


# Main loop: evaluate model first, then backtest
all_analytics = []

for stock, data in stock_data.items():
    analytics = run_backtesting(stock, data)  # Backtest on the entire dataset
    all_analytics.append(analytics)

# Combine all analytics into a single DataFrame
final_analytics_df = pd.concat(all_analytics, ignore_index=True)

# Save the combined DataFrame as a single CSV
final_output_path = "results/lstm_no_commission/combined_analytics.csv"
final_analytics_df.to_csv(final_output_path, index=False)

print(f"Combined analytics CSV saved to {final_output_path}")

Running backtesting for AC...
155/155 [==============================] - 1s 5ms/step
===Strategy level arguments===
Upper limit:  2
Lower limit:  -2


<IPython.core.display.Javascript object>

Running backtesting for ACEN...
149/149 [==============================] - 1s 5ms/step
===Strategy level arguments===
Upper limit:  2
Lower limit:  -2


<IPython.core.display.Javascript object>

Running backtesting for AEV...
154/154 [==============================] - 1s 5ms/step
===Strategy level arguments===
Upper limit:  2
Lower limit:  -2


...

Running backtesting for TEL...
155/155 [==============================] - 1s 5ms/step
===Strategy level arguments===
Upper limit:  2
Lower limit:  -2


<IPython.core.display.Javascript object>

Running backtesting for URC...
149/149 [==============================] - 1s 5ms/step
===Strategy level arguments===
Upper limit:  2
Lower limit:  -2


<IPython.core.display.Javascript object>

Combined analytics CSV saved to results/lstm_no_commission/combined_analytics.csv


In [8]:

# Portfolio-Level Statistics
total_pnl = final_analytics_df['pnl'].sum()
final_portfolio_value = final_analytics_df['final_value'].sum()
average_sharpe_ratio = final_analytics_df['sharperatio'].mean()
average_return = final_analytics_df['rtot'].mean()
average_annualized_return = final_analytics_df['rnorm100'].mean()
max_drawdown = final_analytics_df['maxdrawdown'].max()

# Risk Metrics
total_trades = final_analytics_df['total'].sum()
total_wins = final_analytics_df['won'].sum()
win_rate = total_wins / total_trades if total_trades > 0 else 0
average_loss = final_analytics_df['lost_avg_prcnt'].mean()
max_loss = final_analytics_df['lost_max_prcnt'].min()

# Performance Metrics
most_profitable_stock = final_analytics_df.loc[final_analytics_df['pnl'].idxmax(), 'ticker']
highest_win = final_analytics_df['won_max_prcnt'].max()
most_loss_stock = final_analytics_df.loc[final_analytics_df['lost_avg_prcnt'].idxmin(), 'ticker']


# Print Portfolio Insights
print("Portfolio Insights:")
print(f"Total Profit (PnL): {total_pnl}")
print(f"Final Portfolio Value: {final_portfolio_value}")
print(f"Average Sharpe Ratio: {average_sharpe_ratio}")
print(f"Average Return: {average_return}")
print(f"Average Annualized Return (rnorm100): {average_annualized_return}")
print(f"Max Drawdown: {max_drawdown}")
print(f"Win Rate: {win_rate * 100:.2f}%")
print(f"Average Loss (%): {average_loss}")
print(f"Max Loss (%): {max_loss}")
print(f"Most Profitable Stock: {most_profitable_stock}")
print(f"Highest Win (% Gain): {highest_win}")
print(f"Most Loss (% Stock): {most_loss_stock}")

Portfolio Insights:
Total Profit (PnL): 323903468.96000004
Final Portfolio Value: 325903468.96400005
Average Sharpe Ratio: 0.5230187059724368
Average Return: 3.9764828855665484
Average Annualized Return (rnorm100): 24.17964906047866
Max Drawdown: 91.58770033301647
Win Rate: 73.33%
Average Loss (%): -66.99811289628173
Max Loss (%): -4904.2985999999955
Most Profitable Stock: DMC
Highest Win (% Gain): 34403.91086000001
Most Loss (% Stock): DMC


# SMAC Strategy

In [9]:
import os

# Ensure the results directory exists
results_dir = "results/smac"
os.makedirs(results_dir, exist_ok=True)

# Function to run backtesting using SMAC strategy
def run_backtesting_smac(stock, data, fast_period=50, slow_period=200):
    print(f"Running backtesting for {stock} using SMAC strategy...")
    _, _, _, _, _, _, _, df, _ = data

    # Ensure the dataset has the necessary columns
    if "Close" not in df.columns:
        raise ValueError(f"Data for {stock} must contain a 'Close' column.")

    # Run SMAC backtest
    smac_result, history_dict, fig = backtest(
        "smac",
        data=df,
        fast_period=fast_period,
        slow_period=slow_period,
        return_history=True,
        return_plot=True,
        verbose=False,
        commission=0.006,
        riskfreerate=annual_risk_free_rate_20yr
    )

    # Save plot
    plot_path = os.path.join(results_dir, f"{stock}_plot.png")
    fig.savefig(plot_path, dpi=300, bbox_inches="tight")
    print(f"Saved SMAC plot for {stock} to {plot_path}")
    plt.close(fig)

    # Save order history
    orders_csv_path = os.path.join(results_dir, f"{stock}_orders.csv")
    history_dict["orders"].to_csv(orders_csv_path, index=False)
    print(f"Saved SMAC order history for {stock} to {orders_csv_path}")

    # Extract relevant analytics
    columns_to_keep = [
        "rtot", "ravg", "rnorm", "rnorm100", "len", "drawdown", "moneydown", "maxdrawdown",
        "maxdrawdownperiod", "sharperatio", "pnl", "final_value", "total", "win_rate", "won",
        "lost", "won_avg", "won_avg_prcnt", "lost_avg", "lost_avg_prcnt", "won_max_prcnt",
        "lost_max_prcnt",
    ]
    analytics = smac_result[columns_to_keep]
    analytics["ticker"] = stock

    return analytics

# Main loop: run SMAC backtest for all stocks
all_analytics = []

for stock, data in stock_data.items():
    analytics = run_backtesting_smac(stock, data)  # Run SMAC backtest
    all_analytics.append(analytics)

# Combine all analytics into a single DataFrame
final_analytics_df = pd.concat(all_analytics, ignore_index=True)

# Save the combined DataFrame as a single CSV
final_output_path = os.path.join(results_dir, "combined_analytics.csv")
final_analytics_df.to_csv(final_output_path, index=False)
print(f"Combined analytics CSV saved to {final_output_path}")


Running backtesting for AC using SMAC strategy...


<IPython.core.display.Javascript object>

Saved SMAC plot for AC to results/smac/AC_plot.png
Saved SMAC order history for AC to results/smac/AC_orders.csv
Running backtesting for ACEN using SMAC strategy...


<IPython.core.display.Javascript object>

Saved SMAC plot for ACEN to results/smac/ACEN_plot.png
Saved SMAC order history for ACEN to results/smac/ACEN_orders.csv
Running backtesting for AEV using SMAC strategy...


...

Saved SMAC plot for SMPH to results/smac/SMPH_plot.png
Saved SMAC order history for SMPH to results/smac/SMPH_orders.csv
Running backtesting for TEL using SMAC strategy...


<IPython.core.display.Javascript object>

Saved SMAC plot for TEL to results/smac/TEL_plot.png
Saved SMAC order history for TEL to results/smac/TEL_orders.csv
Running backtesting for URC using SMAC strategy...


<IPython.core.display.Javascript object>

Saved SMAC plot for URC to results/smac/URC_plot.png
Saved SMAC order history for URC to results/smac/URC_orders.csv
Combined analytics CSV saved to results/smac/combined_analytics.csv


In [10]:
# Portfolio-Level Statistics
total_pnl = final_analytics_df['pnl'].sum()
final_portfolio_value = final_analytics_df['final_value'].sum()
average_sharpe_ratio = final_analytics_df['sharperatio'].mean()
average_return = final_analytics_df['rtot'].mean()
average_annualized_return = final_analytics_df['rnorm100'].mean()
max_drawdown = final_analytics_df['maxdrawdown'].max()

# Risk Metrics
total_trades = final_analytics_df['total'].sum()
total_wins = final_analytics_df['won'].sum()
win_rate = total_wins / total_trades if total_trades > 0 else 0
average_loss = final_analytics_df['lost_avg_prcnt'].mean()
max_loss = final_analytics_df['lost_max_prcnt'].min()

# Performance Metrics
most_profitable_stock = final_analytics_df.loc[final_analytics_df['pnl'].idxmax(), 'ticker']
highest_win = final_analytics_df['won_max_prcnt'].max()
most_loss_stock = final_analytics_df.loc[final_analytics_df['lost_avg_prcnt'].idxmin(), 'ticker']


# Print Portfolio Insights
print("Portfolio Insights:")
print(f"Total Profit (PnL): {total_pnl}")
print(f"Final Portfolio Value: {final_portfolio_value}")
print(f"Average Sharpe Ratio: {average_sharpe_ratio}")
print(f"Average Return: {average_return}")
print(f"Average Annualized Return (rnorm100): {average_annualized_return}")
print(f"Max Drawdown: {max_drawdown}")
print(f"Win Rate: {win_rate * 100:.2f}%")
print(f"Average Loss (%): {average_loss}")
print(f"Max Loss (%): {max_loss}")
print(f"Most Profitable Stock: {most_profitable_stock}")
print(f"Highest Win (% Gain): {highest_win}")
print(f"Most Loss (% Stock): {most_loss_stock}")

Portfolio Insights:
Total Profit (PnL): 8931925.120000001
Final Portfolio Value: 10931925.11829
Average Sharpe Ratio: -0.031250957465104076
Average Return: 0.8264990458184261
Average Annualized Return (rnorm100): 4.313326642199419
Max Drawdown: 95.87990229750272
Win Rate: 37.16%
Average Loss (%): -49.35286849280076
Max Loss (%): -308.2185743999998
Most Profitable Stock: DMC
Highest Win (% Gain): 1530.2182414400002
Most Loss (% Stock): DMC


# Bollinger Bands Strategy

In [11]:
import os

# Ensure the results directory exists
results_dir = "results/bbands"
os.makedirs(results_dir, exist_ok=True)

# Function to run backtesting using Bollinger Bands strategy
def run_backtesting_bbands(stock, data, period=20, devfactor=2):
    print(f"Running backtesting for {stock} using Bollinger Bands strategy...")
    _, _, _, _, _, _, _, df, _ = data

    # Ensure the dataset has the necessary columns
    if "Close" not in df.columns:
        raise ValueError(f"Data for {stock} must contain a 'Close' column.")

    # Run Bollinger Bands backtest
    bbands_result, history_dict, fig = backtest(
        "bbands",
        data=df,
        period=period,
        devfactor=devfactor,
        return_history=True,
        return_plot=True,
        verbose=False,
        commission=0.006,  # Optional commission
        riskfreerate=annual_risk_free_rate_20yr
    )

    # Save plot
    plot_path = os.path.join(results_dir, f"{stock}_plot.png")
    fig.savefig(plot_path, dpi=300, bbox_inches="tight")
    print(f"Saved Bollinger Bands plot for {stock} to {plot_path}")
    plt.close(fig)

    # Save order history
    orders_csv_path = os.path.join(results_dir, f"{stock}_orders.csv")
    history_dict["orders"].to_csv(orders_csv_path, index=False)
    print(f"Saved Bollinger Bands order history for {stock} to {orders_csv_path}")

    # Extract relevant analytics
    columns_to_keep = [
        "rtot", "ravg", "rnorm", "rnorm100", "len", "drawdown", "moneydown", "maxdrawdown",
        "maxdrawdownperiod", "sharperatio", "pnl", "final_value", "total", "win_rate", "won",
        "lost", "won_avg", "won_avg_prcnt", "lost_avg", "lost_avg_prcnt", "won_max_prcnt",
        "lost_max_prcnt",
    ]
    analytics = bbands_result[columns_to_keep]
    analytics["ticker"] = stock

    return analytics

# Main loop: run Bollinger Bands backtest for all stocks
all_analytics = []

for stock, data in stock_data.items():
    analytics = run_backtesting_bbands(stock, data)  # Run Bollinger Bands backtest
    all_analytics.append(analytics)

# Combine all analytics into a single DataFrame
final_analytics_df = pd.concat(all_analytics, ignore_index=True)

# Save the combined DataFrame as a single CSV
final_output_path = os.path.join(results_dir, "combined_analytics.csv")
final_analytics_df.to_csv(final_output_path, index=False)
print(f"Combined analytics CSV saved to {final_output_path}")


Running backtesting for AC using Bollinger Bands strategy...


<IPython.core.display.Javascript object>

Saved Bollinger Bands plot for AC to results/bbands/AC_plot.png
Saved Bollinger Bands order history for AC to results/bbands/AC_orders.csv
Running backtesting for ACEN using Bollinger Bands strategy...


<IPython.core.display.Javascript object>

Saved Bollinger Bands plot for ACEN to results/bbands/ACEN_plot.png
Saved Bollinger Bands order history for ACEN to results/bbands/ACEN_orders.csv
Running backtesting for AEV using Bollinger Bands strategy...


...

Saved Bollinger Bands plot for SMPH to results/bbands/SMPH_plot.png
Saved Bollinger Bands order history for SMPH to results/bbands/SMPH_orders.csv
Running backtesting for TEL using Bollinger Bands strategy...


<IPython.core.display.Javascript object>

Saved Bollinger Bands plot for TEL to results/bbands/TEL_plot.png
Saved Bollinger Bands order history for TEL to results/bbands/TEL_orders.csv
Running backtesting for URC using Bollinger Bands strategy...


<IPython.core.display.Javascript object>

Saved Bollinger Bands plot for URC to results/bbands/URC_plot.png
Saved Bollinger Bands order history for URC to results/bbands/URC_orders.csv
Combined analytics CSV saved to results/bbands/combined_analytics.csv


In [12]:
# Portfolio-Level Statistics
total_pnl = final_analytics_df['pnl'].sum()
final_portfolio_value = final_analytics_df['final_value'].sum()
average_sharpe_ratio = final_analytics_df['sharperatio'].mean()
average_return = final_analytics_df['rtot'].mean()
average_annualized_return = final_analytics_df['rnorm100'].mean()
max_drawdown = final_analytics_df['maxdrawdown'].max()

# Risk Metrics
total_trades = final_analytics_df['total'].sum()
total_wins = final_analytics_df['won'].sum()
win_rate = total_wins / total_trades if total_trades > 0 else 0
average_loss = final_analytics_df['lost_avg_prcnt'].mean()
max_loss = final_analytics_df['lost_max_prcnt'].min()

# Performance Metrics
most_profitable_stock = final_analytics_df.loc[final_analytics_df['pnl'].idxmax(), 'ticker']
highest_win = final_analytics_df['won_max_prcnt'].max()
most_loss_stock = final_analytics_df.loc[final_analytics_df['lost_avg_prcnt'].idxmin(), 'ticker']


# Print Portfolio Insights
print("Portfolio Insights:")
print(f"Total Profit (PnL): {total_pnl}")
print(f"Final Portfolio Value: {final_portfolio_value}")
print(f"Average Sharpe Ratio: {average_sharpe_ratio}")
print(f"Average Return: {average_return}")
print(f"Average Annualized Return (rnorm100): {average_annualized_return}")
print(f"Max Drawdown: {max_drawdown}")
print(f"Win Rate: {win_rate * 100:.2f}%")
print(f"Average Loss (%): {average_loss}")
print(f"Max Loss (%): {max_loss}")
print(f"Most Profitable Stock: {most_profitable_stock}")
print(f"Highest Win (% Gain): {highest_win}")
print(f"Most Loss (% Stock): {most_loss_stock}")

Portfolio Insights:
Total Profit (PnL): 341828.19000000006
Final Portfolio Value: 2341828.2027340014
Average Sharpe Ratio: -0.20181728776819977
Average Return: -0.1446008372868121
Average Annualized Return (rnorm100): -0.7893621578682793
Max Drawdown: 92.73795110022478
Win Rate: 61.98%
Average Loss (%): -16.49359183318945
Max Loss (%): -329.23701059999996
Most Profitable Stock: JFC
Highest Win (% Gain): 233.524677
Most Loss (% Stock): BLOOM


# RSI Strategy

In [13]:
import os

# Ensure the results directory exists
results_dir = "results/rsi"
os.makedirs(results_dir, exist_ok=True)

# Function to run backtesting using RSI strategy
def run_backtesting_rsi(stock, data, rsi_period=14, rsi_lower=30, rsi_upper=70):
    print(f"Running backtesting for {stock} using RSI strategy...")
    _, _, _, _, _, _, _, df, _ = data

    # Ensure the dataset has the necessary columns
    if "Close" not in df.columns:
        raise ValueError(f"Data for {stock} must contain a 'Close' column.")

    # Run RSI backtest
    rsi_result, history_dict, fig = backtest(
        "rsi",
        data=df,
        rsi_period=rsi_period,
        rsi_lower=rsi_lower,
        rsi_upper=rsi_upper,
        return_history=True,
        return_plot=True,
        verbose=False,
        commission=0.006,  # Optional commission
        riskfreerate=annual_risk_free_rate_20yr
    )

    # Save plot
    plot_path = os.path.join(results_dir, f"{stock}_plot.png")
    fig.savefig(plot_path, dpi=300, bbox_inches="tight")
    print(f"Saved RSI plot for {stock} to {plot_path}")
    plt.close(fig)

    # Save order history
    orders_csv_path = os.path.join(results_dir, f"{stock}_orders.csv")
    history_dict["orders"].to_csv(orders_csv_path, index=False)
    print(f"Saved RSI order history for {stock} to {orders_csv_path}")

    # Extract relevant analytics
    columns_to_keep = [
        "rtot", "ravg", "rnorm", "rnorm100", "len", "drawdown", "moneydown", "maxdrawdown",
        "maxdrawdownperiod", "sharperatio", "pnl", "final_value", "total", "win_rate", "won",
        "lost", "won_avg", "won_avg_prcnt", "lost_avg", "lost_avg_prcnt", "won_max_prcnt",
        "lost_max_prcnt",
    ]
    analytics = rsi_result[columns_to_keep]
    analytics["ticker"] = stock

    return analytics

# Main loop: run RSI backtest for all stocks
all_analytics = []

for stock, data in stock_data.items():
    analytics = run_backtesting_rsi(stock, data)  # Run RSI backtest
    all_analytics.append(analytics)

# Combine all analytics into a single DataFrame
final_analytics_df = pd.concat(all_analytics, ignore_index=True)

# Save the combined DataFrame as a single CSV
final_output_path = os.path.join(results_dir, "combined_analytics.csv")
final_analytics_df.to_csv(final_output_path, index=False)
print(f"Combined analytics CSV saved to {final_output_path}")


Running backtesting for AC using RSI strategy...


<IPython.core.display.Javascript object>

Saved RSI plot for AC to results/rsi/AC_plot.png
Saved RSI order history for AC to results/rsi/AC_orders.csv
Running backtesting for ACEN using RSI strategy...


<IPython.core.display.Javascript object>

Saved RSI plot for ACEN to results/rsi/ACEN_plot.png
Saved RSI order history for ACEN to results/rsi/ACEN_orders.csv
Running backtesting for AEV using RSI strategy...


...

Saved RSI plot for SMPH to results/rsi/SMPH_plot.png
Saved RSI order history for SMPH to results/rsi/SMPH_orders.csv
Running backtesting for TEL using RSI strategy...


<IPython.core.display.Javascript object>

Saved RSI plot for TEL to results/rsi/TEL_plot.png
Saved RSI order history for TEL to results/rsi/TEL_orders.csv
Running backtesting for URC using RSI strategy...


<IPython.core.display.Javascript object>

Saved RSI plot for URC to results/rsi/URC_plot.png
Saved RSI order history for URC to results/rsi/URC_orders.csv
Combined analytics CSV saved to results/rsi/combined_analytics.csv


In [14]:
# Portfolio-Level Statistics
total_pnl = final_analytics_df['pnl'].sum()
final_portfolio_value = final_analytics_df['final_value'].sum()
average_sharpe_ratio = final_analytics_df['sharperatio'].mean()
average_return = final_analytics_df['rtot'].mean()
average_annualized_return = final_analytics_df['rnorm100'].mean()
max_drawdown = final_analytics_df['maxdrawdown'].max()

# Risk Metrics
total_trades = final_analytics_df['total'].sum()
total_wins = final_analytics_df['won'].sum()
win_rate = total_wins / total_trades if total_trades > 0 else 0
average_loss = final_analytics_df['lost_avg_prcnt'].mean()
max_loss = final_analytics_df['lost_max_prcnt'].min()

# Performance Metrics
most_profitable_stock = final_analytics_df.loc[final_analytics_df['pnl'].idxmax(), 'ticker']
highest_win = final_analytics_df['won_max_prcnt'].max()
most_loss_stock = final_analytics_df.loc[final_analytics_df['lost_avg_prcnt'].idxmin(), 'ticker']


# Print Portfolio Insights
print("Portfolio Insights:")
print(f"Total Profit (PnL): {total_pnl}")
print(f"Final Portfolio Value: {final_portfolio_value}")
print(f"Average Sharpe Ratio: {average_sharpe_ratio}")
print(f"Average Return: {average_return}")
print(f"Average Annualized Return (rnorm100): {average_annualized_return}")
print(f"Max Drawdown: {max_drawdown}")
print(f"Win Rate: {win_rate * 100:.2f}%")
print(f"Average Loss (%): {average_loss}")
print(f"Max Loss (%): {max_loss}")
print(f"Most Profitable Stock: {most_profitable_stock}")
print(f"Highest Win (% Gain): {highest_win}")
print(f"Most Loss (% Stock): {most_loss_stock}")

Portfolio Insights:
Total Profit (PnL): 1415288.69
Final Portfolio Value: 3415288.699912
Average Sharpe Ratio: -0.16271224410269997
Average Return: 0.1699730992416631
Average Annualized Return (rnorm100): 0.7877882049719698
Max Drawdown: 91.53310718
Win Rate: 66.76%
Average Loss (%): -29.802154776240876
Max Loss (%): -160.97906359999996
Most Profitable Stock: BPI
Highest Win (% Gain): 156.63113340000007
Most Loss (% Stock): LTG
